In [1]:
#Set the display into latex form 
%display latex
#Parallel computations
#Parallelism().set(nproc=8)

In [1]:
#Define a 4d manifold with Lorentzian signature
M = Manifold(4, 'M', structure='Lorentzian')
#Define a coordinate X  = (t,r,theta,phi) with specific charts
X.<t,r,th,ph> = M.chart(r"t r:(0,+oo) th:(0,pi):\theta ph:(0,2*pi):\phi")
#Set the perturbation parameters
eps = var('epsilon')
#Define mass parameter 
m = var('m'); assume(m>=0)
#Defining frequency parameters
k = var('k')
#Defining angular momentum 
L = var('L')
#Define scalar functions h0(r), h1(r) in odd perturbation channel as in Eq. (18) of Regge-Wheeler
h0 = function('h_0') 
h1 = function('h_1')

In [3]:
#differentiation of Legendre polynomial
sindP=sin(th)*diff(legendre_P(L,cos(th)),th).full_simplify()
sindP

L*cos(th)*legendre_P(L, cos(th)) - L*legendre_P(L - 1, cos(th))

In [6]:
#Define metric and odd perturbation as in Eq. (18) of Regge-Wheeler from https://doi.org/10.1103/PhysRev.108.1063
g=M.metric()
g[0,0] = -(1-2*m/r)
g[1,1] = 1/(1-2*m/r)
g[2,2] = r^2
g[3,3] = (r*sin(th))^2
g[0,3] = h0(r)*exp(-I*k*t)*sindP*eps
g[1,3] = h1(r)*exp(-I*k*t)*sindP*eps
#Check if the metric that spit out make sense
g[:]

[                                                                                  2*m/r - 1                                                                                           0                                                                                           0 (L*cos(th)*legendre_P(L, cos(th)) - L*legendre_P(L - 1, cos(th)))*epsilon*e^(-I*k*t)*h_0(r)]
[                                                                                          0                                                                              -1/(2*m/r - 1)                                                                                           0 (L*cos(th)*legendre_P(L, cos(th)) - L*legendre_P(L - 1, cos(th)))*epsilon*e^(-I*k*t)*h_1(r)]
[                                                                                          0                                                                                           0                                                                                         r^2                                                                                           0]
[(L*cos(th)*legendre_P(L, cos(th)) - L*legendre_P(L - 1, cos(th)))*epsilon*e^(-I*k*t)*h_0(r) (L*cos(th)*legendre_P(L, cos(th)) - L*legendre_P(L - 1, cos(th)))*epsilon*e^(-I*k*t)*h_1(r)                                                                                           0                                                                               r^2*sin(th)^2]

In [7]:
#First method to get Ricci tensor
g1 =g.truncate(eps, 1) 
gpert = M.lorentzian_metric('g_p')
gpert[:]=g1[:]
%time Ric = gpert.ricci()

KeyboardInterrupt: ECL says: Console interrupt.

In [9]:
#Compute Ricci tensor at first order perturbation in eps -- this take about 3 minutes 
#Set timer for this computation 
#
g.set_calc_order(eps, 1)
%time Ric2 = g.ricci()

CPU times: user 4min 10s, sys: 2.57 s, total: 4min 13s
Wall time: 3min 32s


In [10]:
#Obtain Einstein tensor
%time G = Ric2-1/2*g.ricci_scalar()*g


CPU times: user 5.75 s, sys: 68.7 ms, total: 5.82 s
Wall time: 4.84 s


In [11]:
#simplifying 13 component of Einstein tensor G
coeffdh0G13= G[1,3].expr().coefficient(diff(h0(r),r)).full_simplify()
#normalised G13 by coefficient of dh0
normG13=G[1,3]/coeffdh0G13
coG13h0=normG13.expr().coefficient(h0(r)).full_simplify()
coG13h1=normG13.expr().coefficient(h1(r)).full_simplify()
coG13dh0=normG13.expr().coefficient(diff(h0(r),r)).full_simplify()
coG13dh1=normG13.expr().coefficient(diff(h1(r),r)).full_simplify()
#Coefficients of most of the terms are really simple
coG13h0,coG13dh0,coG13dh1

(-2/r, 1, 0)

In [60]:
#Coefficients of h1(r) in G13 looks really horrible...but its actually very simple when we set some value for L
#Let's work on specific values of L
coG13h1.subs(L==2).full_simplify()

(I*k^2*r^3 + 8*I*m - 4*I*r)/(k*r^3)

In [61]:
#substitute solution for h1 from 13-component of G
solh1=solve(G[1,3].expr()==0, h1(r))
h1(r).substitute(solh1).subs(L==3).full_simplify()

(I*k*r^3*diff(h_0(r), r) - 2*I*k*r^2*h_0(r))/(k^2*r^3 + 20*m - 10*r)

In [64]:
#Simplify expression for 23-component of G
coeffG23=G[2,3].expr().coefficient(diff(h1(r),r))
simpG23 = G[2,3].expr()/coeffG23.full_simplify()
#The expression seems really horrible 
simpG23

(I*L^2*k*r^3*cos(th)^2*e^(-I*k*t)*h_0(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 2*I*L^2*k*r^3*cos(th)*e^(-I*k*t)*h_0(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) - I*L*k*r^3*cos(th)^2*e^(-I*k*t)*h_0(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 4*L^2*m^2*r*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 4*L^2*m*r^2*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + L^2*r^3*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 3*I*L*k*r^3*cos(th)*e^(-I*k*t)*h_0(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) + I*L^2*k*r^3*e^(-I*k*t)*h_0(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 4*L^2*m^2*cos(th)^2*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 2*L^2*m*r*cos(th)^2*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 8*L^2*m^2*r*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 8*L^2*m*r^2*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 2*L^2*r^3*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 4*L*m^2*r*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 4*L*m*r^2*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - L*r^3*cos(th)^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 8*L^2*m^2*cos(th)*e^(-I*k*t)*h_1(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 4*L^2*m*r*cos(th)*e^(-I*k*t)*h_1(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) - I*L*k*r^3*e^(-I*k*t)*h_0(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) - I*L*k*r^3*e^(-I*k*t)*h_0(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 4*L*m^2*cos(th)^2*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 2*L*m*r*cos(th)^2*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 12*L*m^2*r*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 12*L*m*r^2*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 3*L*r^3*cos(th)*e^(-I*k*t)*legendre_P(L - 1, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 4*L^2*m^2*r*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 4*L^2*m*r^2*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + L^2*r^3*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 12*L*m^2*cos(th)*e^(-I*k*t)*h_1(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 6*L*m*r*cos(th)*e^(-I*k*t)*h_1(r)*legendre_P(L - 1, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 4*L^2*m^2*e^(-I*k*t)*h_1(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 2*L^2*m*r*e^(-I*k*t)*h_1(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 4*L*m^2*r*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 4*L*m*r^2*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - L*r^3*e^(-I*k*t)*legendre_P(L - 2, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - 4*L*m^2*r*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 4*L*m*r^2*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) - L*r^3*e^(-I*k*t)*legendre_P(L, cos(th))*diff(h_1(r), r)/((2*m*r^2 - r^3)*sin(th)) + 4*L*m^2*e^(-I*k*t)*h_1(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 2*L*m*r*e^(-I*k*t)*h_1(r)*legendre_P(L - 2, cos(th))/((2*m*r^2 - r^3)*sin(th)) + 4*L*m^2*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)) - 2*L*m*r*e^(-I*k*t)*h_1(r)*legendre_P(L, cos(th))/((2*m*r^2 - r^3)*sin(th)))*epsilon*r*e^(I*k*t)*sin(th)/(2*(L^2*legendre_P(L - 2, cos(th)) - L*legendre_P(L - 2, cos(th)) - L*legendre_P(L, cos(th)))*epsilon*m - (L^2*legendre_P(L - 2, cos(th)) - L*legendre_P(L - 2, co

In [69]:
#but actually, coefficients of h1,h0, h1'(r), h0'(r) 
coh1=simpG23.coefficient(h1(r)).full_simplify()
coh0=simpG23.coefficient(h0(r)).full_simplify()
codh1=simpG23.coefficient(diff(h1(r),r)).full_simplify()
codh0=simpG23.coefficient(diff(h0(r),r)).full_simplify()
#super simplified G23
ssimpG23= coh1*h1(r)+ coh0*h0(r)+ codh1*diff(h1(r),r)+codh0*diff(h0(r),r)
#Print out coefficient of each term
coh0,coh1,codh1,codh0

(I*k*r^2/(4*m^2 - 4*m*r + r^2), -2*m/(2*m*r - r^2), 1, 0)

In [70]:
#This is what the EInstien equation component 23 looks like 
ssimpG23

I*k*r^2*h_0(r)/(4*m^2 - 4*m*r + r^2) - 2*m*h_1(r)/(2*m*r - r^2) + diff(h_1(r), r)

In [76]:
#substitute function h1 to those from 13-component of G
#Here, we will set L=1 for simplicity, if wanted to can chage to differnt L here
h1r(r) = h1(r).substitute(solh1).subs(L==1).full_simplify()
#Define eomh0 as Einstein tensor (23-component) after eliminating h1
eomh0=ssimpG23.substitute_function(h1,h1r).expand()

In [77]:
#Collecting coefficients of each term in eomh0  to see that there is no h1
eomh0.collect(h0(r)).collect(diff(h0(r),r)).collect(diff(h0(r),r,r)).full_simplify()

((I*k^2*r^4 + 16*I*m^2 - 12*I*m*r + 2*I*r^2)*h_0(r) + 2*(-6*I*m^2*r + 5*I*m*r^2 - I*r^3)*diff(h_0(r), r) + (4*I*m^2*r^2 - 4*I*m*r^3 + I*r^4)*diff(h_0(r), r, r))/(4*k*m^2*r^2 - 4*k*m*r^3 + k*r^4)

In [94]:
#Alternatively, we can substitute h0 in terms of h1
solh0 = solve(ssimpG23==0, h0(r))
h0r(r) = h0(r).substitute(solh0)
#Simplify 13-component of G
#Simplify expression for 23-component of G
coeffG13 = G[1,3].expr().coefficient(diff(h0(r),r))
simpG13=(G[1,3].expr())/coeffG13.factor()

In [95]:
#This is a neat form of h1 
eomh1=simpG13.substitute_function(h0,h0r).expand()
eomh1simp=eomh1.collect(h1(r)).collect(diff(h1(r),r)).collect(diff(h1(r),r,r))
eomh1simp.subs(L==2).full_simplify()

((I*k^2*r^4 + 20*I*m^2 - 4*I*r^2)*h_1(r) + 2*(-10*I*m^2*r + 7*I*m*r^2 - I*r^3)*diff(h_1(r), r) + (4*I*m^2*r^2 - 4*I*m*r^3 + I*r^4)*diff(h_1(r), r, r))/(k*r^4)

In [98]:
#Defining the function Q in Eq.(23) of Regge-Wheeler
Q=function('Q')
h1sub(r) = k*r*Q(r)/(1-2*m/r)
eomQ=eomh1simp.substitute_function(h1,h1sub).expand().simplify().collect(Q(r)).collect(diff(Q(r),r)).collect(diff(Q(r),r,r)).full_simplify()
eomQ

((2*(-3*I*L^2*legendre_P(L - 2, cos(th)) + 8*I*L*legendre_P(L - 2, cos(th)) - (I*L^2 - 2*I*L)*legendre_P(L, cos(th)) - 5*I*legendre_P(L - 2, cos(th)))*m*r + (3*I*L^2*legendre_P(L - 2, cos(th)) - 8*I*L*legendre_P(L - 2, cos(th)) + (I*L^2 - 2*I*L)*legendre_P(L, cos(th)) + 5*I*legendre_P(L - 2, cos(th)))*r^2)*Q(r)*cos(th) + ((-I*k^2*r^4*legendre_P(L - 1, cos(th)) + 2*(-3*I*L^2*legendre_P(L - 1, cos(th)) + 4*I*L*legendre_P(L - 1, cos(th)) - 5*I*legendre_P(L - 1, cos(th)))*m*r + (3*I*L^2*legendre_P(L - 1, cos(th)) - 4*I*L*legendre_P(L - 1, cos(th)) + 2*I*legendre_P(L - 1, cos(th)))*r^2 + 12*I*m^2*legendre_P(L - 1, cos(th)))*Q(r) + ((I*k^2*r^4*legendre_P(L, cos(th)) + 2*(I*L^2 + I*L + 3*I)*m*r*legendre_P(L, cos(th)) + (-I*L^2 - I*L)*r^2*legendre_P(L, cos(th)) - 12*I*m^2*legendre_P(L, cos(th)))*Q(r) + 2*(-2*I*m^2*r*legendre_P(L, cos(th)) + I*m*r^2*legendre_P(L, cos(th)))*diff(Q(r), r) + (4*I*m^2*r^2*legendre_P(L, cos(th)) - 4*I*m*r^3*legendre_P(L, cos(th)) + I*r^4*legendre_P(L, cos(th)))*diff(Q(r), r, r))*cos(th) + 2*(2*I*m^2*r*legendre_P(L - 1, cos(th)) - I*m*r^2*legendre_P(L - 1, cos(th)))*diff(Q(r), r) + (-4*I*m^2*r^2*legendre_P(L - 1, cos(th)) + 4*I*m*r^3*legendre_P(L - 1, cos(th)) - I*r^4*legendre_P(L - 1, cos(th)))*diff(Q(r), r, r))*sin(th)^2 - (2*(L^2*(-3*I*legendre_P(L - 1, cos(th)) - I*legendre_P(L - 3, cos(th))) + L*(7*I*legendre_P(L - 1, cos(th)) + 3*I*legendre_P(L - 3, cos(th))) - 3*I*legendre_P(L - 1, cos(th)) - 2*I*legendre_P(L - 3, cos(th)))*m*r - (L^2*(-3*I*legendre_P(L - 1, cos(th)) - I*legendre_P(L - 3, cos(th))) + L*(7*I*legendre_P(L - 1, cos(th)) + 3*I*legendre_P(L - 3, cos(th))) - 3*I*legendre_P(L - 1, cos(th)) - 2*I*legendre_P(L - 3, cos(th)))*r^2)*Q(r))/((2*m*r^2*legendre_P(L - 1, cos(th)) - r^3*legendre_P(L - 1, cos(th)) - (2*m*r^2*legendre_P(L, cos(th)) - r^3*legendre_P(L, cos(th)))*cos(th))*sin(th)^2)

In [99]:
#These coefficients and obviously be simplified 
#Coefficient of d^2Q/dr^2
eomQ.coefficient(diff(Q(r),r,r)).full_simplify()

-2*I*m + I*r

In [100]:
#Coefficient of dQ/dr
eomQ.coefficient(diff(Q(r),r)).full_simplify()

2*I*m/r

In [101]:
#The first line give a total mess 
eomQ.coefficient(Q(r)).full_simplify()
#but upon setting L=1,2 or something reasonable it becomes nicer
eomQ.coefficient(Q(r)).subs(L==2).full_simplify()

(-I*k^2*r^4 + 12*I*m^2 - 18*I*m*r + 6*I*r^2)/(2*m*r^2 - r^3)

In [102]:
#writing dQ/dr in to dQ/dr* and d^2Q/dr^2 in terms of d^2Q/dr*2
rstar = function('r^*')(r)
dQdr=diff(Q(rstar),r).subs(diff(rstar,r)==1/(1-2*m/r))
d2Qdr2= diff(diff(Q(rstar),r).subs(diff(rstar,r)==1/(1-2*m/r)),r).subs(diff(rstar,r)==1/(1-2*m/r))
#Note dQ/dr* and d^2Q/dr*^2
dQdrStar = diff(Q(rstar))/diff(rstar,r)
d2Qdr2Star=diff(dQdrStar)/diff(rstar,r)

In [103]:
#Let's set L=1 in the remianing computations, can change to different value from here 
eomQ.expand().subs(L==1).simplify().factor()

-(I*k^2*r^4*Q(r)*cos(th)^2*sin(th)^2 - I*k^2*r^4*Q(r)*sin(th)^2 + 4*I*m^2*r^2*cos(th)^2*sin(th)^2*diff(Q(r), r, r) - 4*I*m*r^3*cos(th)^2*sin(th)^2*diff(Q(r), r, r) + I*r^4*cos(th)^2*sin(th)^2*diff(Q(r), r, r) - 4*I*m^2*r*cos(th)^2*sin(th)^2*diff(Q(r), r) + 2*I*m*r^2*cos(th)^2*sin(th)^2*diff(Q(r), r) - 12*I*m^2*Q(r)*cos(th)^2*sin(th)^2 + 10*I*m*r*Q(r)*cos(th)^2*sin(th)^2 - 2*I*r^2*Q(r)*cos(th)^2*sin(th)^2 - 4*I*m^2*r^2*sin(th)^2*diff(Q(r), r, r) + 4*I*m*r^3*sin(th)^2*diff(Q(r), r, r) - I*r^4*sin(th)^2*diff(Q(r), r, r) + 4*I*m^2*r*sin(th)^2*diff(Q(r), r) - 2*I*m*r^2*sin(th)^2*diff(Q(r), r) + 2*I*m*r*Q(r)*cos(th)^2 - I*r^2*Q(r)*cos(th)^2 + 12*I*m^2*Q(r)*sin(th)^2 - 8*I*m*r*Q(r)*sin(th)^2 + I*r^2*Q(r)*sin(th)^2 - 2*I*m*r*Q(r) + I*r^2*Q(r))/((2*m - r)*r^2*(cos(th) + 1)*(cos(th) - 1)*sin(th)^2)

In [104]:
rstar = function('r^*')(r)

In [105]:
#THis is the odd channel of Regge-Wheeler equations
eomQrStar=eomQ.subs(diff(Q(r),r)==dQdr).subs(diff(Q(r),r,r)==d2Qdr2).subs(L==1).expand()
#Coefficients of d^2Q/dr^2, dQ/dr and Q. Check that this agrees with Regge-Wheeler's result for 
[eomQrStar.coefficient(d2Qdr2Star).full_simplify(),eomQrStar.coefficient(dQdrStar).full_simplify(),eomQrStar.coefficient(Q(r)).full_simplify()]

[-I*r^2/(2*m - r),
 0,
 (-I*k^2*r^4 + 12*I*m^2 - 10*I*m*r + 2*I*r^2)/(2*m*r^2 - r^3)]